In [1]:
import os
if "ntbk" in os.getcwd():
    os.chdir("..")
print(os.getcwd())

import sys
sys.path.append(os.path.join(os.getcwd(), "otgnn"))


%load_ext autoreload
%autoreload 2

from otgnn.models import GCN
from otgnn.graph import MolGraph
from otgnn.utils import save_model, load_model

from mol_opt.mol_opt import MolOpt
from mol_opt.data_mol_opt import MolOptDataset
from mol_opt.data_mol_opt import get_loader
from mol_opt.arguments import get_args
from mol_opt.train_mol_opt import main, get_latest_model
from mol_opt.ot_utils import compute_barycenter

from rdkit.Chem import MolFromSmiles

import torch
import numpy as np
import time
import torch.nn.functional as F

/home/octav/gitrepos/tum-thesis


In [2]:
model_type = "deepsets"
sys.argv = ["", "-cuda", "-model_type", model_type]
args = get_args()
outdir_suffix = "dev6"
args.n_epochs = 12000 
args.init_model = "{}-gumbel-noanneal".format(model_type)
# args.init_model = "{}-test1".format(model_type)
args.init_decoder_model = "{}_decode".format(args.init_model)
args.output_dir = "mol_opt/output_{}/{}".format(outdir_suffix, args.init_model)
args.tb_logs_dir = "mol_opt/logs_{}/{}".format(outdir_suffix, args.init_model)
args.batch_size = 50 

args.penalty_gumbel = True 

args.scale_lambdas = True
args.connectivity = True 
args.valency = True 
args.euler_characteristic_penalty = True
args.conn_lambda_start = 0.001
args.conn_lambda_end = 3
args.conn_lambda_epochs_start = 3001
args.conn_lambda_epochs_end = 8000
args.valency_lambda_start = 0.001
args.valency_lambda_end = 5
args.valency_lambda_epochs_start = 3001
args.valency_lambda_epochs_end = 8000
args.euler_lambda_start = 0.001 
args.euler_lambda_end = 2 
args.euler_lambda_epochs_start = 3001
args.euler_lambda_epochs_end = 8000
args.tau_start = 1
args.tau_end = 1
args.tau_epochs_start = 1
args.tau_epochs_end = 8000

args.cross_att_use = False
args.cross_att_random = False
args.cross_att_n_sinkhorn = 1
args.cross_att_use_gcn2 = True
args.cross_att_sigmoid = False
args.ot_lambda = -0.1
# args.morgan_bits = 1024

# args.fgw_no_bonds = False

args.conn_penalty_function = "capped_logdet" 

print(args, '\n')

Namespace(N_transformer=6, agg_func='sum', batch_norm=False, batch_size=50, conn_lambda_end=3, conn_lambda_epochs_end=8000, conn_lambda_epochs_start=3001, conn_lambda_start=0.001, conn_penalty_function='capped_logdet', connectivity=True, connectivity_hard=False, cross_att_dim=150, cross_att_n_sinkhorn=1, cross_att_random=False, cross_att_sigmoid=False, cross_att_use=False, cross_att_use_gcn2=True, cuda=True, device='cuda:0', dim_tangent_space=40, dropout_ffn=0.0, dropout_gcn=0.0, dropout_transformer=0.1, euler_characteristic_penalty=True, euler_lambda_end=2, euler_lambda_epochs_end=8000, euler_lambda_epochs_start=3001, euler_lambda_start=0.001, ffn_activation='LeakyReLU', fgw_atoms=True, fgw_bonds=True, init_decoder_model='deepsets-gumbel-noanneal_decode', init_model='deepsets-gumbel-noanneal', linear_out=False, max_num_atoms=70, model_type='deepsets', morgan_bits=0, n_epochs=12000, n_ffn_hidden=100, n_ffn_transformer=100, n_heads_transformer=10, n_hidden=200, n_labels=1, n_layers=5, o

In [3]:
# train_data_loader = get_loader("iclr19-graph2graph/data/qed", "train_pairs", args.batch_size, same_number_atoms = True)
# train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("iclr19-graph2graph/data/qed", "valid", 36, False)

train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("molgen/data/chembl50", "val_split", args.batch_size, same_number_atoms = True)
val_data_loader = None

In [4]:
molopt, molopt_decoder = main(args, train_data_loader = train_data_loader, val_data_loader = val_data_loader)

Found previous model mol_opt/output_dev6/deepsets-gumbel-noanneal/model_deepsets-gumbel-noanneal_3082, epoch 3082. Overwriting args.
Penalty params: tau=1.00000 conn_l=0.00114 val_l=0.00115 euler_l=0.00113 epoch=3082 mode=[1 1 1] conn=True val=True euler=True
Epoch: 3083


/home/octav/gitrepos/tum-thesis/otgnn/models/gromov_modules.py:398: UserWarning: Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.
  nce_reg = torch.nn.LogSoftmax()(torch.stack(all_nce_dists))[0]


Losses Batch 0, train
 fgw:0.1763284
 conn_penalty:0.8646871
 val_penalty:4.9947531
 euler_penalty:1.8862941
 total:0.1851805
Penalty params: tau=1.00000 conn_l=0.00114 val_l=0.00115 euler_l=0.00113 epoch=3083 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=1.00000 conn_l=0.00114 val_l=0.00115 euler_l=0.00113 epoch=3083 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 3083, train
 fgw:0.1763284
 conn_penalty:0.8646871
 val_penalty:4.9947531
 euler_penalty:1.8862941
 total:0.1851805
Saving model, do not interrupt...
Saved at mol_opt/output_dev6/deepsets-gumbel-noanneal/model_deepsets-gumbel-noanneal_3083
Epoch duration: 3.752717971801758
Epoch: 3084
Losses Batch 0, train
 fgw:0.1754137
 conn_penalty:1.0568396
 val_penalty:3.6342322
 euler_penalty:0.5839242
 total:0.1814596
Penalty params: tau=1.00000 conn_l=0.00114 val_l=0.00115 euler_l=0.00113 epoch=3084 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=1.00000 conn_l=0.00114 val_l=0.00115 euler_l=0.0

Losses Batch 0, train
 fgw:0.1684358
 conn_penalty:0.5780012
 val_penalty:6.0118915
 euler_penalty:2.8194226
 total:0.1794168
Penalty params: tau=1.00000 conn_l=0.00116 val_l=0.00118 euler_l=0.00116 epoch=3096 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=1.00000 conn_l=0.00116 val_l=0.00118 euler_l=0.00116 epoch=3096 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 3096, train
 fgw:0.1684358
 conn_penalty:0.5780012
 val_penalty:6.0118915
 euler_penalty:2.8194226
 total:0.1794168
Saving model, do not interrupt...
Saved at mol_opt/output_dev6/deepsets-gumbel-noanneal/model_deepsets-gumbel-noanneal_3096
Epoch duration: 4.313405990600586
Epoch: 3097
Losses Batch 0, train
 fgw:0.1769028
 conn_penalty:1.9884595
 val_penalty:1.9981731
 euler_penalty:0.3091190
 total:0.1819246
Penalty params: tau=1.00000 conn_l=0.00117 val_l=0.00118 euler_l=0.00116 epoch=3097 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=1.00000 conn_l=0.00117 val_l=0.00118 euler_l=0.0

Losses Batch 0, train
 fgw:0.1741488
 conn_penalty:0.2562036
 val_penalty:15.9750232
 euler_penalty:11.0620740
 total:0.2066402
Penalty params: tau=1.00000 conn_l=0.00119 val_l=0.00120 euler_l=0.00118 epoch=3109 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=1.00000 conn_l=0.00119 val_l=0.00120 euler_l=0.00118 epoch=3109 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 3109, train
 fgw:0.1741488
 conn_penalty:0.2562036
 val_penalty:15.9750232
 euler_penalty:11.0620740
 total:0.2066402
Saving model, do not interrupt...
Saved at mol_opt/output_dev6/deepsets-gumbel-noanneal/model_deepsets-gumbel-noanneal_3109
Epoch duration: 5.570179224014282
Epoch: 3110
Losses Batch 0, train
 fgw:0.1895870
 conn_penalty:3.3666794
 val_penalty:2.1943013
 euler_penalty:1.7841394
 total:0.1983298
Penalty params: tau=1.00000 conn_l=0.00119 val_l=0.00120 euler_l=0.00118 epoch=3110 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=1.00000 conn_l=0.00119 val_l=0.00120 euler_l

...

Losses Batch 0, train
 fgw:0.7596745
 conn_penalty:0.0000000
 val_penalty:0.0655779
 euler_penalty:0.0661096
 total:1.2197832
Penalty params: tau=1.00000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10453 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=1.00000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10453 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 10453, train
 fgw:0.7596745
 conn_penalty:0.0000000
 val_penalty:0.0655779
 euler_penalty:0.0661096
 total:1.2197832
Saving model, do not interrupt...
Saved at mol_opt/output_dev6/deepsets-gumbel-noanneal/model_deepsets-gumbel-noanneal_10453
Epoch duration: 3.6788434982299805
Epoch: 10454
Losses Batch 0, train
 fgw:0.7558282
 conn_penalty:0.0320255
 val_penalty:0.0564038
 euler_penalty:0.0592921
 total:1.2525079
Penalty params: tau=1.00000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10454 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=1.00000 conn_l=3.00000 val_l=5.00000 eule

Losses Batch 0, train
 fgw:0.7359726
 conn_penalty:0.0000000
 val_penalty:0.0847950
 euler_penalty:0.0673680
 total:1.2946835
Penalty params: tau=1.00000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10465 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=1.00000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10465 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 10465, train
 fgw:0.7359726
 conn_penalty:0.0000000
 val_penalty:0.0847950
 euler_penalty:0.0673680
 total:1.2946835
Saving model, do not interrupt...
Saved at mol_opt/output_dev6/deepsets-gumbel-noanneal/model_deepsets-gumbel-noanneal_10465
Epoch duration: 5.711053848266602
Epoch: 10466
Losses Batch 0, train
 fgw:0.7387922
 conn_penalty:0.0640509
 val_penalty:0.0658972
 euler_penalty:0.0974848
 total:1.4554005
Penalty params: tau=1.00000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10466 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=1.00000 conn_l=3.00000 val_l=5.00000 euler

Losses Batch 0, train
 fgw:0.7392467
 conn_penalty:0.0320255
 val_penalty:0.0845533
 euler_penalty:0.0465925
 total:1.3512746
Penalty params: tau=1.00000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10477 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=1.00000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10477 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 10477, train
 fgw:0.7392467
 conn_penalty:0.0320255
 val_penalty:0.0845533
 euler_penalty:0.0465925
 total:1.3512746
Saving model, do not interrupt...
Saved at mol_opt/output_dev6/deepsets-gumbel-noanneal/model_deepsets-gumbel-noanneal_10477
Epoch duration: 4.610576629638672
Epoch: 10478
Losses Batch 0, train
 fgw:0.7447977
 conn_penalty:0.0000000
 val_penalty:0.0870725
 euler_penalty:0.0698095
 total:1.3197794
Penalty params: tau=1.00000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10478 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=1.00000 conn_l=3.00000 val_l=5.00000 euler

Losses Batch 0, train
 fgw:0.7357646
 conn_penalty:0.0000000
 val_penalty:0.0792244
 euler_penalty:0.1085766
 total:1.3490399
Penalty params: tau=1.00000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10489 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=1.00000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10489 mode=[0 0 0] conn=True val=True euler=True
Losses Epoch 10489, train
 fgw:0.7357646
 conn_penalty:0.0000000
 val_penalty:0.0792244
 euler_penalty:0.1085766
 total:1.3490399
Saving model, do not interrupt...
Saved at mol_opt/output_dev6/deepsets-gumbel-noanneal/model_deepsets-gumbel-noanneal_10489
Epoch duration: 3.542238712310791
Epoch: 10490
Losses Batch 0, train
 fgw:0.7309870
 conn_penalty:0.0000000
 val_penalty:0.0853149
 euler_penalty:0.0650233
 total:1.2876080
Penalty params: tau=1.00000 conn_l=3.00000 val_l=5.00000 euler_l=2.00000 epoch=10490 mode=[0 0 0] conn=True val=True euler=True
Penalty params: tau=1.00000 conn_l=3.00000 val_l=5.00000 euler

KeyboardInterrupt: 